In [135]:
import os
import pickle
import numpy as np
from rdkit import Chem
from rdkit.Chem import AllChem
import ZMPY3D as zm
from pathlib import Path

import math


In [136]:
import pickle #из библиотеки, загрузка кеша

MaxOrder=6

# Find the cache_data directory based on the site package location of ZMPY3D.
BinomialCacheFilePath=zm.__file__.replace('__init__.py', 'cache_data') + '/BinomialCache.pkl'
with open(BinomialCacheFilePath, 'rb') as file:
    BinomialCachePKL = pickle.load(file)

LogCacheFilePath=zm.__file__.replace('__init__.py', 'cache_data') + '/LogG_CLMCache_MaxOrder{:02d}.pkl'.format(MaxOrder)
with open(LogCacheFilePath, 'rb') as file:
    CachePKL = pickle.load(file)

BinomialCache=BinomialCachePKL['BinomialCache']

GCache_pqr_linear=CachePKL['GCache_pqr_linear']
GCache_complex=CachePKL['GCache_complex']
GCache_complex_index=CachePKL['GCache_complex_index']
CLMCache3D=CachePKL['CLMCache3D']
CLMCache=CachePKL['CLMCache']
RotationIndex=CachePKL['RotationIndex']

s_id=np.squeeze(RotationIndex['s_id'][0,0])-1
n   =np.squeeze(RotationIndex['n'][0,0])
l   =np.squeeze(RotationIndex['l'][0,0])
m   =np.squeeze(RotationIndex['m'][0,0])
mu  =np.squeeze(RotationIndex['mu'][0,0])
k   =np.squeeze(RotationIndex['k'][0,0])
IsNLM_Value=np.squeeze(RotationIndex['IsNLM_Value'][0,0])-1


In [137]:
def zernike_rotation_invariant_from_raw(ZMoment_raw, n_arr, l_arr, m_arr):
    """
    Делает rotation-invariant дескриптор:
        D_{n,l} = sqrt( sum_{m=-l..l} |Z_{n,l,m}|^2 )

    Предполагается, что ZMoment_raw — 1D массив комплексных чисел,
    а n_arr/l_arr/m_arr — 1D массивы индексов той же длины.
    """
    Z = np.asarray(ZMoment_raw).reshape(-1)
    n_arr = np.asarray(n_arr).reshape(-1)
    l_arr = np.asarray(l_arr).reshape(-1)
    m_arr = np.asarray(m_arr).reshape(-1)

    if not (len(Z) == len(n_arr) == len(l_arr) == len(m_arr)):
        raise ValueError(f"Lengths mismatch: Z={len(Z)} n={len(n_arr)} l={len(l_arr)} m={len(m_arr)}")

    # Берём только допустимые (n,l) в пределах MaxOrder.
    # В RotationIndex обычно уже всё согласовано, но оставим фильтр на всякий случай.
    # (Если хочешь, можно убрать.)
    mask = (n_arr >= 0) & (l_arr >= 0)
    Z = Z[mask]; n_arr = n_arr[mask]; l_arr = l_arr[mask]

    # Группируем по (n,l) и суммируем |Z|^2
    pairs = np.stack([n_arr, l_arr], axis=1)  # shape (N,2)
    uniq_pairs, inv = np.unique(pairs, axis=0, return_inverse=True)

    energy = np.zeros(len(uniq_pairs), dtype=np.float64)
    np.add.at(energy, inv, np.abs(Z)**2)

    descriptor = np.sqrt(energy)

    # Чтобы вектор был стабильным по порядку — сортируем пары (n,l)
    order = np.lexsort((uniq_pairs[:, 1], uniq_pairs[:, 0]))
    uniq_pairs = uniq_pairs[order]
    descriptor = descriptor[order]

    return descriptor, [tuple(p) for p in uniq_pairs]


In [138]:
#from library
def OneTimeConversionInvariant(
        Voxel3D, Corner, GridWidth,
        GCache_complex, GCache_complex_index, GCache_pqr_linear,
        CLMCache3D,
        MaxOrder, Param,
        n_arr, l_arr, m_arr,
        normalize=True
):
    Dimension_BBox_scaled = Voxel3D.shape

    XYZ_SampleStruct = {
        'X_sample': np.arange(Dimension_BBox_scaled[0] + 1),
        'Y_sample': np.arange(Dimension_BBox_scaled[1] + 1),
        'Z_sample': np.arange(Dimension_BBox_scaled[2] + 1)
    }

    # 1) центр масс
    VolumeMass, Center, _ = zm.calculate_bbox_moment(Voxel3D, 1, XYZ_SampleStruct)

    # 2) радиус
    AverageVoxelDist2Center, MaxVoxelDist2Center = zm.calculate_molecular_radius(
        Voxel3D, Center, VolumeMass, Param['default_radius_multiplier']
    )

    Center_scaled = Center * GridWidth + Corner

    # 3) веса для сферы
    SphereXYZ_SampleStruct = zm.get_bbox_moment_xyz_sample(
        Center, AverageVoxelDist2Center, Dimension_BBox_scaled
    )

    # 4) геом. моменты
    _, _, SphereBBoxMoment = zm.calculate_bbox_moment(Voxel3D, MaxOrder, SphereXYZ_SampleStruct)

    # 5) сырые Zernike моменты
    _, ZMoment_raw = zm.calculate_bbox_moment_2_zm(
        MaxOrder,
        GCache_complex, GCache_pqr_linear, GCache_complex_index,
        CLMCache3D,
        SphereBBoxMoment
    )

    # 6) rotation-invariant дескриптор
    desc, nl_pairs = zernike_rotation_invariant_from_raw(ZMoment_raw, n_arr, l_arr, m_arr)

    if normalize:
        # удобно для cosine similarity и для сравнения разных молекул по масштабу
        desc = desc / (np.linalg.norm(desc) + 1e-12)

    return Center_scaled, desc, nl_pairs


In [139]:
Param = {
    'default_radius_multiplier': 1.6,
}

In [140]:
def get_molecule_params_and_coords(mol):

   # Извлекает координаты и уникальные свойства атомов из объекта RDKit mol.

    pt = Chem.GetPeriodicTable()

    # 1. Получаем координаты
    conf = mol.GetConformer()
    xyz = conf.GetPositions()

    # 2. Собираем данные об атомах
    atom_symbols = []
    unique_elements = set()

    for atom in mol.GetAtoms():
        symbol = atom.GetSymbol()
        atom_symbols.append(symbol)
        unique_elements.add(symbol)


    radius_map = {}

    for symbol in unique_elements:
        # Ван-дер-Ваальсов радиус
        radius_map[symbol] = pt.GetRvdw(symbol)

    return xyz, atom_symbols, radius_map


In [141]:
def create_hard_voxel_from_sdf(mol, grid_width=0.1):

    if mol.GetNumConformers() == 0:
        AllChem.EmbedMolecule(mol, AllChem.ETKDG())

    pt = Chem.GetPeriodicTable()
    conf = mol.GetConformer()
    xyz = conf.GetPositions()

    center_mass = np.mean(xyz, axis=0)
    # Центрируем координаты для вокселизации
    xyz_centered = xyz - center_mass

    #Определение размеров куба
    max_dist = np.max(np.linalg.norm(xyz_centered, axis=1))
    cube_side_angstrom = (max_dist + 3.0) * 2
    cube_size = int(np.ceil(cube_side_angstrom / grid_width))

    voxel_cube = np.zeros((cube_size, cube_size, cube_size), dtype=np.float32)
    # Индекс центрального вокселя
    grid_center = cube_size // 2

    #координата [0,0,0] вокселя
    corner_xyz = center_mass - (grid_center * grid_width)


    # Заполнение кубиками
    for i, atom in enumerate(mol.GetAtoms()):
        symbol = atom.GetSymbol()
        weight = 1.0
        radius = pt.GetRvdw(symbol)

        # Позиция центра атома в индексах сетки
        atom_grid_pos = np.round(xyz_centered[i] / grid_width).astype(int) + grid_center

        r_vox = int(np.ceil(radius / grid_width))
        z, y, x = np.ogrid[-r_vox : r_vox+1, -r_vox : r_vox+1, -r_vox : r_vox+1]
        dist_sq = (x**2 + y**2 + z**2) * (grid_width**2)
        mask = dist_sq <= (radius**2)

        # Границы вставки (защиту от выхода за края массива лучше оставить)
        z_s, z_e = atom_grid_pos[0]-r_vox, atom_grid_pos[0]+r_vox+1
        y_s, y_e = atom_grid_pos[1]-r_vox, atom_grid_pos[1]+r_vox+1
        x_s, x_e = atom_grid_pos[2]-r_vox, atom_grid_pos[2]+r_vox+1

        # Вставляем значения
        voxel_cube[z_s:z_e, y_s:y_e, x_s:x_e][mask] = weight

    return voxel_cube, corner_xyz


In [142]:
GridWidth = 1.0


# Загрузка молекулы
mol2 = Chem.MolFromXYZFile("H2O2.xyz")

mol = Chem.SDMolSupplier("H2O_3D.sdf", removeHs=False)[0]
#mol = Chem.MolFromXYZFile(str(MOL_A))
#mol = Chem.MolFromXYZBlock(MOL_A)
XYZ, AtomList, RadiusMap = get_molecule_params_and_coords(mol)

voxelcube, corner = create_hard_voxel_from_sdf(mol)

XYZ1, AtomList1, RadiusMap1 = get_molecule_params_and_coords(mol2)

voxelcube1, corner1 = create_hard_voxel_from_sdf(mol2)


In [143]:
Center_scaled_A, desc_A, nl_A = OneTimeConversionInvariant(
    voxelcube, corner, 0.50,
    GCache_complex, GCache_complex_index, GCache_pqr_linear,
    CLMCache3D,
    MaxOrder, Param,
    n, l, m
)

Center_scaled_A1, desc_A1, nl_A1 = OneTimeConversionInvariant(
    voxelcube1, corner1, 0.50,
    GCache_complex, GCache_complex_index, GCache_pqr_linear,
    CLMCache3D,
    MaxOrder, Param,
    n, l, m
)



ValueError: Lengths mismatch: Z=343 n=794 l=794 m=794

In [132]:
import plotly.graph_objects as go
voxel = voxelcube1
# Создаем координатную сетку
x, y, z = np.meshgrid(
    np.arange(voxel.shape[0]),
    np.arange(voxel.shape[1]),
    np.arange(voxel.shape[2]),
    indexing='ij'  # важно для правильного порядка
)

# Преобразуем в 1D массивы
x_flat = x.flatten()
y_flat = y.flatten()
z_flat = z.flatten()
values_flat = voxel.flatten()
# Визуализация
fig = go.Figure(data=go.Isosurface(
    x=x_flat,
    y=y_flat,
    z=z_flat,
    value=values_flat,
    isomin=voxel.mean(),  # Попробуйте разные значения
    isomax=voxel.max() * 0.5,  # Половина от максимума
    surface_count=3,  # Количество изоповерхностей
    opacity=0.6,
    caps=dict(x_show=False, y_show=False, z_show=False),
    colorscale='viridis'
))

fig.update_layout(
    scene=dict(
        xaxis_title='X',
        yaxis_title='Y',
        zaxis_title='Z',
        aspectratio=dict(x=1, y=1, z=1)
    ),
    title=f"3D Voxel Visualization: {voxel.shape}"
)

fig.show()


In [133]:
ZMList_A

array([[ 4.83461106e-01+0.00000000e+00j,  4.83461106e-01+0.00000000e+00j,
         4.83461106e-01+0.00000000e+00j, ...,
         4.83461106e-01+0.00000000e+00j,  4.83461106e-01+0.00000000e+00j,
         4.83461106e-01+0.00000000e+00j],
       [-3.88559715e-01-2.20140018e-16j, -3.88559715e-01-2.20140018e-16j,
        -3.88559715e-01-2.20140018e-16j, ...,
        -3.88559715e-01-2.20140018e-16j, -3.88559715e-01-2.20140018e-16j,
        -3.88559715e-01-2.20140018e-16j],
       [-4.65862888e-02-3.78097602e-16j, -4.65862888e-02-3.78097602e-16j,
        -4.65862888e-02-3.78097602e-16j, ...,
        -4.65862888e-02-3.78097602e-16j, -4.65862888e-02-3.78097602e-16j,
        -4.65862888e-02-3.78097602e-16j],
       ...,
       [-3.49009207e-18+3.06861701e-04j, -2.21846774e-17-3.06861701e-04j,
        -2.96406717e-19+3.06861701e-04j, ...,
         2.17798831e-16+4.04165511e-04j, -2.29809367e-16-4.04165511e-04j,
         2.26697563e-16+4.04165511e-04j],
       [-3.77647914e-03+1.50302195e-17j,  3.

In [134]:
ZMList_A1

array([[ 4.45112100e-01+0.00000000e+00j,  4.45112100e-01+0.00000000e+00j,
         4.45112100e-01+0.00000000e+00j, ...,
         4.45112100e-01+0.00000000e+00j,  4.45112100e-01+0.00000000e+00j,
         4.45112100e-01+0.00000000e+00j],
       [-3.57233747e-01-2.02392169e-16j, -3.57233747e-01-2.02392169e-16j,
        -3.57233747e-01-2.02392169e-16j, ...,
        -3.57233747e-01-2.02392169e-16j, -3.57233747e-01-2.02392169e-16j,
        -3.57233747e-01-2.02392169e-16j],
       [-1.31621648e-02-3.58167598e-16j, -1.31621648e-02-3.58167598e-16j,
        -1.31621648e-02-3.58167598e-16j, ...,
        -1.31621648e-02-3.58167598e-16j, -1.31621648e-02-3.58167598e-16j,
        -1.31621648e-02-3.58167598e-16j],
       ...,
       [-2.94761994e-03+9.96418274e-05j,  2.94761994e-03-9.96418274e-05j,
         2.94251545e-03-1.05514101e-04j, ...,
         1.12754447e-03+2.64341875e-04j, -1.09711176e-03+1.92049157e-04j,
         1.09711176e-03-1.92049157e-04j],
       [ 3.51797169e-03-6.74381552e-04j, -3.